# Alimentador descriptores de obra

Notebook para crear los descriptores y vincularlos a las obras.  Necesita dos tablas. Una que contiene los ids de las obras a crear y otra que contiene la relación de los descriptores y obras del excel de Arca

In [2]:
import os
import json
import numpy as np
import requests
import pandas as pd
from dotenv import load_dotenv

## Abrir tablas y filtrar datos

In [4]:
load_dotenv()
#carga la configuracion
config = json.load(open('../config/config.json'))

descriptores_tabla = '../datos/entrada/csv/Descriptores_registros_1.csv'


descriptores = pd.read_csv(descriptores_tabla, dtype=str)

descriptores = descriptores.dropna(how='all')
descriptores = descriptores.sort_values(by='id')
filtrar = False

if filtrar:
    obras_tabla = '../tablas/csv/obra-soluciones.csv'
    # dataframes de las tablas
    obras = pd.read_csv(obras_tabla, dtype=str)
    #filtrar los descriptores por los ids de obras en arca
    descriptores_filtrados = descriptores.loc[descriptores['artwork_id'].isin(obras['arca_id']).tolist()]

    #muestra para prueba
    #descriptores_filtrados = descriptores_filtrados.sample(1)
    #descriptores_filtrados
    discriptores = descriptores_filtrados
    print(len(descriptores_filtrados.index))

## URLS

In [5]:
#baseurl = 'http://localhost:8055/'
baseurl = config['baseurl']
obra_descriptor_baseurl = f'{baseurl}items/obra_descriptores_lista'
obras_url = f'{baseurl}items/obra'
descriptores_url = f'{baseurl}items/descriptores_lista'

key = os.getenv('KEY')
headers =  {'Authorization':f'Bearer {key}'}

## Iteración

In [4]:
for index, row in descriptores.iterrows():
    obra_arcaID = row['artwork_id']
    descriptor_arcaID = row['description_id']
    obra_url = f'{obras_url}?filter[arca_id][_eq]={obra_arcaID}&limit=1'
    desc_url = f'{descriptores_url}?filter[arca_id][_eq]={descriptor_arcaID}&limit=1'
    m2m_arcaid = row['id']
    #obra = {}
    #descriptor = {}

    #obtener la obra de la api
    try:
        r_obra = requests.get(obra_url)
        r_obra.raise_for_status()
        print(f'econtrada obra: {obra_arcaID}')
    except requests.RequestException as err:
        print(f'Error obteniendo obra: {obra_arcaID}')
        print(err)
        # si se produce error, continua el siguiente registro
        continue

    #se obtienen los datos de la respuesta
    try:
        obra = r_obra.json()['data'][0]
        #print(obra)
    except IndexError as e:
        print(e)
        continue
    #obtener el descriptor de la api
    try: 
        r_desc = requests.get(desc_url)
        r_desc.raise_for_status()
    except requests.RequestException as err:
        print(f'Error obteniendo descripcion: {descriptor_arcaID}')
        print(err)
        continue

    #se obtienen los datos de la respuesta
    try:
        descriptor = r_desc.json()['data'][0]
        #print(descriptor)
    except IndexError as e:
        print(e)
        continue

    # crear el objeto obra descriptor con los ids de los objetos viculados
    obra_desc = {}
    obra_desc['obra_id'] = obra['id']
    obra_desc['descriptores_lista_id'] = descriptor['id']
    
    # crear m2m obra descriptor
    try:
        r_obdesc_m2m = requests.post(obra_descriptor_baseurl, 
            json = obra_desc,
            headers=headers
        )
        r_obdesc_m2m.raise_for_status()
    except requests.RequestException as err:
        print(f'Error creando m2m obra desctripcion: {obra_desc}')
        print(err)
        continue

    obdesc_m2m = r_obdesc_m2m.json()['data']
    m2mid = obdesc_m2m['id']
    print(f'Creada relacion obra descriptor{m2mid} arcaid {m2m_arcaid}')
    #print(obdesc_m2m)

econtrada obra: 834
Creada relacion obra descriptor272 arcaid 10
econtrada obra: 802
Creada relacion obra descriptor273 arcaid 1000
econtrada obra: 5250
Creada relacion obra descriptor274 arcaid 100000
econtrada obra: 6409
Creada relacion obra descriptor275 arcaid 100002
econtrada obra: 6409
Creada relacion obra descriptor276 arcaid 100004
econtrada obra: 5251
Creada relacion obra descriptor277 arcaid 100006
econtrada obra: 6410
Creada relacion obra descriptor278 arcaid 100009
econtrada obra: 5252
Creada relacion obra descriptor279 arcaid 100011
econtrada obra: 6458
Creada relacion obra descriptor280 arcaid 100016
econtrada obra: 6458
Creada relacion obra descriptor281 arcaid 100017
econtrada obra: 6459
Creada relacion obra descriptor282 arcaid 100018
econtrada obra: 6459
Creada relacion obra descriptor283 arcaid 100020
econtrada obra: 5253
Creada relacion obra descriptor284 arcaid 100022
econtrada obra: 5253
Creada relacion obra descriptor285 arcaid 100025
econtrada obra: 6460
Creada 